## 2 Ground Control Stations (simple)

This is a first version. The two ground control stations are working in series. 

In [14]:
from config import Color
from helpers import clean, local2global
from plan import Plan
from simulators import QGC, ConfigGazebo, Gazebo, Simulator

clean()

## Create Plans

In [15]:
offsets = [  # east, north, up, heading
    (0., 0., 0., 0.),
    (10., 0., 0., 45.),
    (-5., -10., 0., 225.),
    (-15., 0., 0., 0.),
    (0., -20., 0., 0.),
]
n_blue_veh = 2

n_vehicles = len(offsets)
side_lens = (5, 5, 5, 5, 5)  # must agree with n_vehicles
local_paths = [Plan.create_square_path(side_len=side_len, alt=5) for side_len in side_lens]
plans = [Plan.basic(wps=path, wp_margin=0.5) for path in local_paths]

## Visualization Parameters

In [16]:

homes = [offset[:3] for offset in offsets]
global_paths = [local2global(path, home) for path, home in zip(local_paths, homes)]
models = n_blue_veh*[('iris',Color.BLUE)]+(n_vehicles-n_blue_veh)*[('iris',Color.GREEN)]
markers = [ConfigGazebo.create_trajectory_from_array(array=global_paths[i],color=models[i][1]) for i in range(n_vehicles)]
Gazebo.plot_3d_interactive(markers=markers, title="Simulation Markers", frames=(0.2, 0.2, 0.6), ground=-0.05)

## Choose Simulator

In [ ]:
simulator = QGC(offsets=offsets, 
                plans=plans,
                origin=(-35.3633245, 149.1652241, 0, 0),
                visible_terminals=False)


simulator = Simulator(offsets=offsets, plans=plans,visible_terminals=False)

gazebo_config = ConfigGazebo(world_path="simulators/gazebo/worlds/runway.world",
                             models=models,
                             markers = markers)
simulator = Gazebo(offsets=offsets,plans=plans,config=gazebo_config,visible_terminals=False)

Launch Simulator

In [18]:
sysids = list(range(1,n_vehicles+1))
gcs_sysids={'blue 🟦':sysids[:n_blue_veh],'green 🟩':sysids[n_blue_veh:]}
orac = simulator.launch(gcs_sysids)

🚀 ArduPilot SITL vehicle 2 launched (PID 499809)
🚀 ArduPilot SITL vehicle 3 launched (PID 499812)
🚀 ArduPilot SITL vehicle 1 launched (PID 499811)
🚀 ArduPilot SITL vehicle 4 launched (PID 499813)
🚀 ArduPilot SITL vehicle 5 launched (PID 499814)
🚀 UAV logic for vehicle 2 launched (PID 499816)
🔗 UAV logic 2 is connected to Ardupilot SITL vehicle 2
🚀 UAV logic for vehicle 3 launched (PID 499817)
🔗 UAV logic 3 is connected to Ardupilot SITL vehicle 3
🚀 UAV logic for vehicle 1 launched (PID 499819)
🔗 UAV logic 1 is connected to Ardupilot SITL vehicle 1
🚀 UAV logic for vehicle 4 launched (PID 499820)
🔗 UAV logic 4 is connected to Ardupilot SITL vehicle 4
🚀 UAV logic for vehicle 5 launched (PID 499821)
🔗 UAV logic 5 is connected to Ardupilot SITL vehicle 5
SIM_VEHICLE: Start
SIM_VEHICLE: Starting up at [-35.363414332037046, 149.1651690219361, 0.0, 225.0]
SIM_VEHICLE: Using defaults from (../../ardupilot/Tools/autotest/default_params/copter.parm)
SIM_VEHICLE: Adding parameters from (/home/ubun

## Execute Plans

In [19]:
while len(orac.conns):
    for sysid in list(orac.conns.keys()):
        if orac.is_plan_done(sysid):
            orac.remove(sysid)

⌛ Waiting for EKF to be ready... Pending: POS_HORIZ_ABS
⌛ Waiting for EKF to be ready... Pending: POS_HORIZ_ABS
⬅️ GCS ← VEH 3: EKF_STATUS_REPORT
⬅️ ORC ← VEH 3: EKF_STATUS_REPORT
⌛ Waiting for EKF to be ready... Pending: POS_HORIZ_ABS
⌛ Waiting for EKF to be ready... Pending: POS_HORIZ_ABS
⬅️ GCS ← VEH 2: HEARTBEAT
⬅️ ORC ← VEH 2: HEARTBEAT
⬅️ GCS ← VEH 2: EKF_STATUS_REPORT
⬅️ ORC ← VEH 2: EKF_STATUS_REPORT
⬅️ GCS ← VEH 1: HEARTBEAT
⬅️ ORC ← VEH 1: HEARTBEAT
🔗 UAV logic 1 is connected
⬅️ GCS ← VEH 4: SYSTEM_TIME
⬅️ ORC ← VEH 4: SYSTEM_TIME
⬅️ GCS ← VEH 3: SYSTEM_TIME
⬅️ ORC ← VEH 3: SYSTEM_TIME
⬅️ GCS ← VEH 4: STATUSTEXT
⬅️ ORC ← VEH 4: STATUSTEXT
⬅️ GCS ← VEH 1: STATUSTEXT
⬅️ ORC ← VEH 1: STATUSTEXT
⬅️ GCS ← VEH 5: STATUSTEXT
⬅️ ORC ← VEH 5: STATUSTEXT
⬅️ GCS ← VEH 2: STATUSTEXT
⬅️ ORC ← VEH 2: STATUSTEXT
⬅️ GCS ← VEH 1: TIMESYNC
⬅️ ORC ← VEH 1: TIMESYNC
⬅️ GCS ← VEH 1: HEARTBEAT
⬅️ ORC ← VEH 1: HEARTBEAT
⬅️ GCS ← VEH 1: EKF_STATUS_REPORT
⬅️ ORC ← VEH 1: EKF_STATUS_REPORT
⬅️ GCS ← VE

## Print Positions gathered

In [20]:
import pickle
from typing import List

import numpy as np
from numpy.typing import NDArray

colors=[Color.BLUE,Color.GREEN] 
for gcs_name,color in zip(gcs_sysids,colors):
    with open(f"trajectories_{gcs_name}.pkl", "rb") as f:
        trajs = pickle.load(f)
    paths:List[NDArray[np.float64]] = []
    for sysid,path in trajs.items():
        paths.append(np.array([x for x in path if x is not None]))
    markers = [ConfigGazebo.create_trajectory_from_array(array=path,color=color) for path in paths]
    Gazebo.plot_3d_interactive(markers=markers,title="Simulation Waypoints",frames=(0.2, 0.2, 0.6),ground=-0.05)

📤 GCS ← UAV 1: Sending DONE (attempt 2)
📤 GCS ← UAV 1: Sending DONE (attempt 3)
📤 GCS ← UAV 1: Sending DONE (attempt 4)
📤 GCS ← UAV 1: Sending DONE (attempt 5)
📤 GCS ← UAV 1: Sending DONE (attempt 6)
📤 GCS ← UAV 1: Sending DONE (attempt 7)
📤 GCS ← UAV 1: Sending DONE (attempt 8)
📤 GCS ← UAV 1: Sending DONE (attempt 9)
📤 GCS ← UAV 1: Sending DONE (attempt 10)
📤 GCS ← UAV 1: Sending DONE (attempt 11)
✅ Vehicle 1 completed its mission
✅ All UAVs assigned to GCS blue 🟦 have completed their mission.
✅ ACK received. DONE message acknowledged.
❎ Vehicle 1 logic stopped.
💾 Trajectories saved to 'trajectories_blue 🟦.pkl'.
